In [1]:
using JuMP
using GLPK
using Plots; plotly()

Plots.PlotlyBackend()

# Numerical Optimization with JuMP
"Julia for Mathematical Programming" is an open source modeling language for solving various types of optimization problems. It plugs into state of the art and commercial solvers for each type of problem. To start, we can use a solver called GLPK, which is a solver focused on linear programming. 

## Linear Programming
Say we have the problem, 

$$
\begin{align}
\min_{x, y} \qquad & 12x + 20y \\
\textrm{s.t.} \qquad & 6x + 8y \geq 100 \\
& 7x + 12y \geq 120 \\
& x \geq 0\\
& y \in [0, 3]
\end{align}
$$

In [2]:
# first lets plot the function
linear_program(x, y) = 12x + 20y
con1(x, y) = 6x + 8y - 100
con2(x, y) = 7x + 12y - 120

plot_linear_program = function()
    low, high, n = -20, 20, 10
    step = (high - low)/ n
    x = low:step:high
    y = low/4:step:high/4
    
    xlim = 0:step:20
    ylim = 0:step:4
    # not sure if this is correct...doesn't seem to match the answer
    print((Array(x)))
    surface(Array(x), Array(y), linear_program, color=:blues)
    surface!(xlim, ylim, con1, color=:reds)
    surface!(xlim, ylim, con2, color=:greens)
end
plot_linear_program()

[-20.0, -16.0, -12.0, -8.0, -4.0, 0.0, 4.0, 8.0, 12.0, 16.0, 20.0]

We can see that the three regions overlap, and there will be a minimum somewhere in the overlapping area. 

In [3]:
# we can solve this with GLPK and JuMP like so: 
model = Model(GLPK.Optimizer)
# we define the problem with the following macros
# variables with upper and lower bounds
@variable(model, x ≥ 0)
@variable(model, 0 ≤ y ≤ 3)
# function to minimize
@objective(model, Min, 12x + 20y)
# constraints on the system
@constraint(model, c1, 6x + 8y ≥ 100)
@constraint(model, c2, 7x + 12y ≥120)
# optimize the objective
print(model)
optimize!(model)
# show intermediate steps
@show termination_status(model)
@show primal_status(model)
@show dual_status(model)
@show objective_value(model)
@show value(x)
@show value(y)
@show shadow_price(c1)
@show shadow_price(c2)

termination_status(model) = MathOptInterface.OPTIMAL
primal_status(model) = MathOptInterface.FEASIBLE_POINT
dual_status(model) = MathOptInterface.FEASIBLE_POINT
objective_value(model) = 204.99999999999997
value(x) = 15.000000000000005
value(y) = 1.249999999999996
shadow_price(c1) = -0.24999999999999922
shadow_price(c2) = -1.5000000000000007


-1.5000000000000007

The termination status tells us why the solver stopped. Code of `OPTIMAL` means it found a solution. We also found a feasible point for the primal and dual variables in the optimiziation. Knowing that we found an optimal solution and both primal and dual feasible points means that we can query the variables and objective functions. 

The shadow price is the instantaneous change in the objective value of the optimal solution obtained by changing the right hand side constraint by one unit.

We can visualize the job the optimizer has done by looking at the optimized point and the surface plots. Since we rearranged the constraints to be put in terms of zero: 

$$
c_1(x, y) = 6x + 8y - 100 \geq 0 \\
c_2(x, y) = 7x + 12y - 120 \geq 0
$$

In [4]:
plot_linear_program()
x = value(x)
y = value(y)

scatter!([x], [y], [objective_value(model)], label="Objective optimum")
# we can look at the objective with the values of x, y on each constraint as well
scatter!([x], [y], [con1(x, y)], label="Constraint intersection")

[-20.0, -16.0, -12.0, -8.0, -4.0, 0.0, 4.0, 8.0, 12.0, 16.0, 20.0]

## Mixed Integer Linear Programming
Here's an example called the cannery problem from [2]. 

In [5]:
function example_cannery()
    # Origin plants.
    plants = ["Seattle", "San-Diego"]
    num_plants = length(plants)
    # Destination markets.
    markets = ["New-York", "Chicago", "Topeka"]
    num_markets = length(markets)
    # Capacity and demand in cases.
    capacity = [350, 600]
    demand = [300, 300, 300]
    # Distance in thousand miles.
    distance = [2.5 1.7 1.8; 2.5 1.8 1.4]
    # Cost per case per thousand miles.
    freight = 90
    cannery = Model()
    set_optimizer(cannery, GLPK.Optimizer)
    # Create decision variables.
    @variable(cannery, ship[1:num_plants, 1:num_markets] >= 0)
    # Ship no more than plant capacity
    @constraint(
        cannery, capacity_con[i = 1:num_plants], sum(ship[i, :]) <= capacity[i]
    )
    # Ship at least market demand
    @constraint(
        cannery, demand_con[j = 1:num_markets], sum(ship[:, j]) >= demand[j]
    )
    # Minimize transportation cost
    @objective(
        cannery,
        Min,
        sum(
            distance[i, j] * freight * ship[i, j]
            for i = 1:num_plants, j = 1:num_markets
        )
    )
    print(cannery)
    optimize!(cannery)
    println("RESULTS:")
    for i = 1:num_plants
        for j = 1:num_markets
            println("  $(plants[i]) $(markets[j]) = $(value(ship[i, j]))")
        end
    end
    return
end

example_cannery()

RESULTS:
  Seattle New-York = 50.0
  Seattle Chicago = 300.0
  Seattle Topeka = 0.0
  San-Diego New-York = 250.0
  San-Diego Chicago = 0.0
  San-Diego Topeka = 300.0


## Quadratic Program
Solving a quadratic program can be done like this. 

In [6]:
using JuMP
import Ipopt
import Test


model = Model(Ipopt.Optimizer)
set_silent(model)
@variable(model, x)
@variable(model, y >= 0)
@variable(model, z >= 0)
@objective(model, Max, x)
@constraint(model, x + y + z == 1)
@constraint(model, x * x + y * y - z * z <= 0)
@constraint(model, x * x - y * z <= 0)
optimize!(model)
print(model)
println("Objective value: ", objective_value(model))
println("x = ", value(x))
println("y = ", value(y))
opt_x = value(x)
opt_y = value(y)
Test.@test termination_status(model) == MOI.LOCALLY_SOLVED
Test.@test primal_status(model) == MOI.FEASIBLE_POINT
Test.@test objective_value(model) ≈ 0.32699 atol = 1e-5
Test.@test value(x) ≈ 0.32699 atol = 1e-5
Test.@test value(y) ≈ 0.25707 atol = 1e-5


******************************************************************************
This program contains Ipopt, a library for large-scale nonlinear optimization.
 Ipopt is released as open source code under the Eclipse Public License (EPL).
         For more information visit https://github.com/coin-or/Ipopt
******************************************************************************

Objective value: 0.32699283491387243
x = 0.32699283491387243
y = 0.2570658388068964


Test Passed

In [8]:
con1(x, y) = 1.0 - x - y
con2(x, y) = sqrt(x^2 + y^2)
con3(x, y) = x^2/y

function plot_quad()
    x = -10:0.1:10
    y = 0:0.05:10
    surface(x, y, con1, color=:blues, zlim=(0, 10))
    surface!(x, y, con2, color=:reds)
    surface!(x, y, con3, color=:greens)
end
# so the optimization problem asks what is the largest x value that exists in this space?
plot_quad()
scatter!([opt_x], [opt_y], [con1(opt_x, opt_y)])

# References
1. JuMP Tutorials. _Getting Started with JuMP_. [JuMP](https://jump.dev/JuMP.jl/stable/)
2. Dantzig, _LinearProgramming and Extensions_, Princeton University Press, Princeton, NJ, 1963. 